In [1]:
#import PyHyperScattering
!pip install PyHyperScattering/
!pip install --pre --upgrade tiled databroker
!pip install xarray==2022.3

Processing ./PyHyperScattering
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for PyHyperScattering: filename=PyHyperScattering-0.1.8+0.gb86d80f.dirty-py3-none-any.whl size=53438 sha256=98483f148eb28a3b7c8bc93a9860e02b5b3d8d4f78809fd93a69d09576aef4a7
  Stored in directory: /tmp/pip-ephem-wheel-cache-n850zr5t/wheels/97/0b/00/3f854164f1750049b0599d676f1b042ba859c61c8fa2285ab5
Successfully built PyHyperScattering
  Attempting uninstall: PyHyperScattering
    Found existing installation: PyHyperScattering 0.1.8+0.gb86d80f.dirty
    Uninstalling PyHyperScattering-0.1.8+0.gb86d80f.dirty:
      Successfully uninstalled PyHyperScattering-0.1.8+0.gb86d80f.dirty


In [2]:
%%capture
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from matplotlib.colors import LogNorm
import PyHyperScattering
load = PyHyperScattering.load.SST1RSoXSDB(corr_mode='none')

### Load stack from scan number

In [3]:
SAXSstack_P90 = load.loadSeries([39810],'sample_name')

/srv/conda/envs/notebook/lib/python3.9/site-packages/PyHyperScattering/SST1RSoXSDB.py:226: UserWarning: Error while time-integrating onto images.  Check data.
  monitors = self.loadMonitors(run)
/srv/conda/envs/notebook/lib/python3.9/site-packages/PyHyperScattering/SST1RSoXSDB.py:188: UserWarning: Error assigning monitor readings to system.  Problem with monitors.  Please check.
  loaded = self.loadRun(self.c[run],**loadrun_kwargs).unstack('system')


### Pick an energy at which to draw the mask
It seems that for some reason the method 'nearest' broke from the old code; so here, I have just made it so that you're getting the precise key out.

In [4]:
energies = np.asarray(SAXSstack_P90.energy)
draw_energy = energies[4]
print(f'Drawing on {draw_energy} eV image')

Drawing on 282.2 eV image


### Make a draw object from your 2D scattering image

In [5]:
test_img = SAXSstack_P90.unstack('system').sel(energy=draw_energy).sel(sample_name='CB_JZ_1PC_386K')##note that you need sample name right here
draw = PyHyperScattering.IntegrationUtils.DrawMask(test_img)

### Use the UI to draw the mask

In [6]:
draw.ui()
# It will lead you through

Usage: click the "PolyAnnotator" tool at top right.  DOUBLE CLICK to start drawing a masked object, SINGLE CLICK to add a vertex, then DOUBLE CLICK to finish.  Click/drag individual vertex to adjust.


:Layout
   .DynamicMap.I :DynamicMap   []
      :Overlay
         .Image.I    :Image   [pix_y,pix_x]   (value)
         .Polygons.I :Polygons   [x,y]   (Label,Value)
   .Annotator.I  :Overlay
      .Table.PolyAnnotator          :Table   [Label]
      .Table.PolyAnnotator_Vertices :Table   [x,y]   (Value)

### Once you're satisfied, save the mask (the draw object is the mask)|

In [7]:
mask_folder = '/where/you/want/to/store/masks/'
draw.save(mask_folder)

FileNotFoundError: [Errno 2] No such file or directory: '/where/you/want/to/store/masks/'

### To continue with the workflow:
Set up the integrator

In [ ]:
integ = PyHyperScattering.integrate.PFEnergySeriesIntegrator(geomethod='template_xr',template_xr = SAXSstack_P90)
integ.ni_beamcenter_x = 390.84 # values for October 2022 SST1 run
integ.ni_beamcenter_y = 555.18

Load up the mask from the filepath (obviously you don't have to do this if you generated it above) and update the integrator with it

In [ ]:
draw.load(f'{mask_folder}maskname.json')
integ.mask = draw.mask

### Check that the mask and beam center work

In [ ]:
PyHyperScattering.IntegrationUtils.Check.checkAll(integ,test_img,img_min=10,img_max=100)

### If they don't, you can reiterate updating the integrator's beam center and try again

In [ ]:
integ.ni_beamcenter_x = 390.84 # values for October 2022 SST1 run
integ.ni_beamcenter_y = 555.18

PyHyperScattering.IntegrationUtils.Check.checkAll(integ,test_img,img_min=10,img_max=100)